# Exploratory Data Analysis of Used Car Listings

## Introduction
This project aims to analyze a dataset of used car advertisements in the US. The dataset contains various attributes such as price, model year, condition, mileage (odometer), and more. The goal is to explore data distribution, identify patterns, and assess data quality before further processing.

### Key Objectives:
- Check for missing values and handle them appropriately.
- Identify potential data inconsistencies.
- Analyze the relationships between price, condition, mileage, and other factors.
- Provide insights that could be useful for pricing models or understanding market trends.

In [1]:
import pandas as pd
import plotly.express as px

In [2]:
df = pd.read_csv('../vehicles_us.csv')

In [3]:
df.head()

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


The dataset contains 51,525 rows and 13 columns, including car prices, model year, mileage (odometer), fuel type, condition, and days listed on the platform.
The dataset consists of both numerical and categorical variables.

In [5]:
df.describe()

price    model_year     cylinders       odometer   is_4wd  \
count   51525.000000  47906.000000  46265.000000   43633.000000  25572.0   
mean    12132.464920   2009.750470      6.125235  115553.461738      1.0   
std     10040.803015      6.282065      1.660360   65094.611341      0.0   
min         1.000000   1908.000000      3.000000       0.000000      1.0   
25%      5000.000000   2006.000000      4.000000   70000.000000      1.0   
50%      9000.000000   2011.000000      6.000000  113000.000000      1.0   
75%     16839.000000   2014.000000      8.000000  155000.000000      1.0   
max    375000.000000   2019.000000     12.000000  990000.000000      1.0   

       days_listed  
count  51525.00000  
mean      39.55476  
std       28.20427  
min        0.00000  
25%       19.00000  
50%       33.00000  
75%       53.00000  
max      271.00000

Car prices vary widely between $1 and $375,000, with an average of $12,132. The high standard deviation suggests significant variability.
Some model years date back to 1908, which is likely an error (needs verification).
Odometer readings have a max value of 990,000 miles, which is extremely high and may indicate an incorrect entry

In [6]:
duplicates = df.duplicated().sum()
print(f'Number of duplicate rows: {duplicates}')

Number of duplicate rows: 0


In [7]:
df.isna().sum()

price               0
model_year       3619
model               0
condition           0
cylinders        5260
fuel                0
odometer         7892
transmission        0
type                0
paint_color      9267
is_4wd          25953
date_posted         0
days_listed         0
dtype: int64

* model_year has 3619 missing values, which could impact trend analysis for price over time.
* cylinders is missing in 5260 cases. This could be imputed based on car model information.
* odometer has missing values in 7892 cases, meaning some cars do not have mileage recorded.
* paint_color is missing in 9267 cases, which may suggest incomplete records from sellers.
* is_4wd is missing in 25953 cases, possibly indicating that 4WD is only marked for cars that have it, while missing values could mean the car is not 4WD.

### Handling Missing Data  
- **is_4wd**: Missing values will be assumed to indicate that the vehicle is not 4WD and will be replaced with `0`.  
- **paint_color**: Missing values will be filled with `'Unknown'`, as they likely represent cases where the seller did not specify the color.  
- **model_year, odometer, cylinders**: Missing values will be restored based on the median values within the same car model.  


In [8]:
df['is_4wd'] = df['is_4wd'].fillna(0)

In [9]:
df['paint_color'] = df['paint_color'].fillna('Unknown')

In [10]:
df['model_year'] = df['model_year'].fillna(df.groupby('model')['model_year'].transform('median'))
df['odometer'] = df['odometer'].fillna(df.groupby('model')['odometer'].transform('median'))
df['cylinders'] = df['cylinders'].fillna(df.groupby('model')['cylinders'].transform('median'))

In [11]:
df.isna().sum()

price            0
model_year       0
model            0
condition        0
cylinders        0
fuel             0
odometer        41
transmission     0
type             0
paint_color      0
is_4wd           0
date_posted      0
days_listed      0
dtype: int64

After applying the median odometer values by model, there are still 41 missing values in the odometer column.

In [12]:
df[df['odometer'].isna()]['model'].value_counts()

model
mercedes-benz benze sprinter 2500    41
Name: count, dtype: int64

These missing values remain because all records for the "mercedes-benz benze sprinter 2500" model originally had no odometer data. Since the median for this model is also NaN, the missing values could not be filled automatically.

To resolve this, we will replace all remaining missing odometer values with the overall median odometer value from the entire dataset. This approach ensures that missing values are filled with a reasonable estimate based on the general distribution of vehicle mileage.

In [13]:
median_van_odometer = df[df['type'] == 'van']['odometer'].median()
df.loc[df['model'] == 'mercedes-benz benze sprinter 2500', 'odometer'] = df.loc[df['model'] == 'mercedes-benz benze sprinter 2500', 'odometer'].fillna(median_van_odometer)

In [14]:
df.isna().sum()

price           0
model_year      0
model           0
condition       0
cylinders       0
fuel            0
odometer        0
transmission    0
type            0
paint_color     0
is_4wd          0
date_posted     0
days_listed     0
dtype: int64

In [15]:
fig_price = px.histogram(df, x='price', nbins=50, title='Distribution of Car Prices')
fig_price.show()

Most vehicles are priced under $50,000, with a few extreme outliers exceeding $300,000.
The distribution is heavily skewed toward lower prices, which aligns with the used car market.

In [16]:
fig_odometer = px.histogram(df, x='odometer', nbins=50, title='Distribution of Odometer Readings')
fig_odometer.show()

Most cars have odometer readings below 200,000 miles, which is expected.
Some vehicles exceed 800,000 miles, which is extremely rare but possible for commercial vehicles or taxis.

In [17]:
fig_scatter = px.scatter(df, x='odometer', y='price', title='Price vs Odometer', trendline='ols')
fig_scatter.show()

A clear negative correlation: higher mileage leads to lower prices.
Some expensive cars with high mileage exist, likely due to rare/luxury brands retaining value despite usage.

In [18]:
fig_condition = px.box(df, x='condition', y='price', title='Price Distribution by Condition')
fig_condition.show()

New cars and "excellent" condition cars have the highest median prices.
Outliers in "good" and "excellent" categories suggest pricing inconsistencies, possibly affected by brand prestige.

In [19]:
fig_fuel = px.bar(df.groupby('fuel', as_index=False)['price'].mean(), 
                  x='fuel', y='price', 
                  title='Average Price by Fuel Type')
fig_fuel.show()


Diesel cars are the most expensive.
Electric vehicles are cheaper on average, but the dataset may lack premium EV models (e.g., Tesla).

In [20]:
fig_year_price = px.scatter(df, x='model_year', y='price', title='Car Price vs Model Year', trendline='ols')
fig_year_price.show()

Newer cars generally have higher prices, but there are exceptions:
Some older models (pre-1980) remain valuable, likely classic cars.
A few modern vehicles (2015+) have surprisingly low prices, indicating possible mispricing or salvage titles.

The dataset has missing values that maybe should be handled.
Price outliers exist; filtering out extreme values may be necessary.
The dataset captures expected trends, such as:
* Mileage negatively impacting price.
* Newer models being more expensive.
* Condition and fuel type influencing cost.